In [1]:
from datasets import load_dataset
import spacy
from transformers import AutoTokenizer, AutoModel
import fasttext.util
from sklearn.metrics.pairwise import cosine_similarity

# SCIBERT modeli için gerekli işlemler
print(1)
# tokenizer = AutoTokenizer.from_pretrained('allenai/scibert_scivocab_uncased',force_download=True)
# model = AutoModel.from_pretrained('allenai/scibert_scivocab_uncased',force_download=True)
print(2)
# Huggingface'deki veri setini yükle
dataset = load_dataset("memray/krapivin")
# Kullanıcı listesi oluşturuluyor
# users = [
#     {
#         "first_name": "Alice",
#         "last_name": "Johnson",
#         "birth_date": "1990-05-15",
#         "gender": "Female",
#         "email": "alice.johnson@example.com",
#         "interests": ["artificial intelligence", "machine learning", "data mining"]
#     },
#     {
#         "first_name": "Bob",
#         "last_name": "Smith",
#         "birth_date": "1985-08-25",
#         "gender": "Male",
#         "email": "bob.smith@example.com",
#         "interests": ["computer graphics", "virtual reality"]
#     },
#     {
#         "first_name": "Carol",
#         "last_name": "White",
#         "birth_date": "1992-11-30",
#         "gender": "Female",
#         "email": "carol.white@example.com",
#         "interests": ["neuroscience", "cognitive science"]
#     }
# ]
users = [
    {"first_name": "Alice", "last_name": "Johnson", "interests": ["artificial intelligence", "machine learning", "data mining"]}
]

print(3)
# spaCy'nin İngilizce dil modelini yükle
nlp = spacy.load("en_core_web_sm")

# spaCy'nin İngilizce dil modelini yükle
def preprocess_text(text):
    # Metni işle
    doc = nlp(text)
    # Stopwords'ü çıkar, lemmatize et ve noktalama işaretlerini çıkar
    cleaned_text = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct]
    # Listeyi string'e çevir
    cleaned_text = " ".join(cleaned_text)
    return cleaned_text
print(4)
# FastText vektör temsili metotu
fasttext.util.download_model('en', if_exists='ignore')  # İngilizce modeli indir
ft_model = fasttext.load_model('cc.en.300.bin')
print(5)
def get_fasttext_vector(text):
    return ft_model.get_sentence_vector(text)

# SCIBERT vektör temsili metotu
tokenizer = AutoTokenizer.from_pretrained('allenai/scibert_scivocab_uncased')
scibert_model = AutoModel.from_pretrained('allenai/scibert_scivocab_uncased')
print(6)
def get_scibert_vector(text):
    inputs = tokenizer(text, return_tensors='pt', padding=True, truncation=True, max_length=512)
    outputs = scibert_model(**inputs)
    # Çıktının son katmanının ortalamasını al
    return outputs.last_hidden_state.mean(dim=1).detach().numpy()

# Cosine similarity hesaplama
def get_recommendations(user_vector, article_vectors):
    similarities = {title: cosine_similarity([user_vector], [vec])[0][0] for title, vec in article_vectors.items()}
    # Benzerlik skorlarına göre sırala ve en yüksek skorlu 5 makaleyi getir
    recommended_articles = sorted(similarities.items(), key=lambda item: item[1], reverse=True)[:5]
    return recommended_articles

# Dataset'ten ilk makalenin özetini al ve ön işleme uygula
# sample_abstract = dataset['validation'][0]['abstract']
# processed_text = preprocess_text(sample_abstract)
# print("Orijinal Metin:", sample_abstract)
# print("İşlenmiş Metin:", processed_text)

# for user in users:
#     interests_text = ' '.join(user['interests'])
#     fasttext_vector = get_fasttext_vector(interests_text)
#     scibert_vector = get_scibert_vector(interests_text)
#     print(f'User: {user["first_name"]} {user["last_name"]}')
#     print('FastText Vector:', fasttext_vector)
#     print('SCIBERT Vector:', scibert_vector)

# article_vectors_fasttext = {article['title']: get_fasttext_vector(article['abstract']) for article in dataset['validation']}
# article_vectors_scibert = {article['title']: get_scibert_vector(article['abstract']) for article in dataset['validation']}

# interests_text = ' '.join(users[0]['interests'])
# user_vector_fasttext = get_fasttext_vector(interests_text)
# user_vector_scibert = get_scibert_vector(interests_text)

# recommendsByFastText = get_recommendations(user_vector_fasttext, article_vectors_fasttext)
# recommendsBySciBert = get_recommendations(user_vector_scibert, article_vectors_scibert)

article_vectors_fasttext = {}
article_vectors_scibert = {}

for article in dataset['test']:
    try:
        title = article['title']
        abstract = article['abstract']
        article_vectors_fasttext[title] = get_fasttext_vector(abstract)
        article_vectors_scibert[title] = get_scibert_vector(abstract)
        print(article_vectors_fasttext[title])
        print(article_vectors_scibert[title])
    except TypeError as e:
        print(f"Error processing article: {article}")
        print(f"TypeError: {e}")

print('Makale vektör temsillerini çıkartma işlemi bitti.')

# interests_text = ' '.join(users[0]['interests'])
# user_vector_fasttext = get_fasttext_vector(interests_text)
# user_vector_scibert = get_scibert_vector(interests_text)

# print('Kullanıcı vektör temsillerini çıkartma işlemi bitti.')

# recommendsByFastText = get_recommendations(user_vector_fasttext, article_vectors_fasttext)
# recommendsBySciBert = get_recommendations(user_vector_scibert, article_vectors_scibert)

# print('Önerileri alma işlemleri bitti..')

# print(recommendsByFastText)
# print(recommendsBySciBert)




1
2
3
4
5


/Users/umut/Desktop/Python Prototype/myenv/lib/python3.12/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


6
[-3.24593261e-02  1.37230624e-02  1.03527624e-02  4.34751026e-02
 -9.69047099e-03  2.31486768e-03  3.39943841e-02 -1.10938512e-02
 -8.83355038e-04 -1.20432731e-02 -3.76217882e-03 -1.07278908e-03
  1.75925829e-02  1.19154714e-02 -3.39567140e-02 -1.62211377e-02
  3.28416675e-02  2.02257317e-02  1.78886000e-02  2.49018281e-04
 -5.62305469e-03 -1.81575119e-02 -7.85876065e-03  3.53607326e-03
 -1.79788889e-03 -2.64566392e-02  9.18460265e-03  1.51060531e-02
  4.37119231e-03  4.28479984e-02  1.00373551e-02 -6.47439901e-03
  5.77053521e-03 -5.46766967e-02  1.60961449e-02  1.13360668e-02
 -9.73467622e-03  1.17310416e-02 -6.52154908e-03 -1.50453276e-03
 -6.18663058e-03 -1.59157589e-02  6.44682162e-03 -1.58067187e-03
 -2.84466390e-02  5.50642563e-03 -4.37401282e-03 -5.50996140e-03
 -1.99883152e-03  2.46430803e-02  8.33530352e-03  1.43388461e-03
 -8.52657613e-05 -1.17739076e-02  1.05192875e-02  9.75537405e-05
  8.29441473e-04  4.68445942e-04 -5.73282950e-02 -2.30590347e-03
  1.60922401e-03 -1.753

In [1]:
interests_text = ' '.join(users[0]['interests'])
interests_text = interests_text + dataset['test'][0]['keyword']
user_vector_fasttext = get_fasttext_vector(interests_text)
user_vector_scibert = get_scibert_vector(interests_text)
interests_text

NameError: name 'users' is not defined

In [21]:
recomm_fasttext = get_recommendations(user_vector_fasttext,article_vectors_fasttext)

In [22]:
recomm_fasttext

[('Enhancing Product Recommender Systems on Sparse Binary Data.', 0.99938196),
 ('Corpus structure, language models, and ad hoc information retrieval.',
  0.96831965),
 ('Collaborative Filtering with Maximum Entropy.', 0.96252173),
 ('An Experimental Comparison of Min-Cut/Max-Flow Algorithms for Energy Minimization in Vision.',
  0.9621008),
 ('A Framework for Resource-Constrained Rate-Optimal Software Pipelining.',
  0.9606778)]